# Final Project Experimental Code
**Bill Xia**<br>
CS 136: Statistical Pattern Recognition<br>
Created: 4/9/24

**Purpose:** A space to test ideas for the Stat Pat Rec final project. Successful ideas will be cleaned up and put together in a separate document.

**TODO:**
- Augment counting system.
    - Whenever you increment, increment the whole column. That is, ignore previous label.
    - Initialize eta_counts such that `I` never comes after `O`.

## Baseline
Here's a basic overview of the baseline prediction algorithm:
```python
import numpy as np

labels = [0, 1, 2]  # Corresponds to ['O', 'B', 'I']
label_preds = []

for idx, w_t in enumerate(words):
    # We want argmax_l[ CatPMF( w_t, l_t | pairList[idx-1] ) ].
    # We break apart the large PMF into two components:
    #   CatPMF(w_t | pi) * CatPMF(l_t | eta)

    # Assuming CatPMF is already implemented, we construct an objective function.
    objective_fun = lambda l: CatPMF(w_t | pi) * CatPMF(l | eta)

    # Get results for all labels.
    label_results = [objective_fun(l) for l in labels]

    # Find the label with the highest probability of occurring.
    best_l = np.argmax(label_results)

    # Add the label to the predictions.
    label_preds.append(best_l)
```

In [1]:
# Imports
import json
import string
import numpy as np
import random

### Training
The first step in getting the baseline working will be to initialize our parameters $\pi$ and $\eta$. This will require us to go through the data and use counts to construct the probability matrices.

In [2]:
# Let's start by loading in the data and making sure that there's nothing
# obviously wrong with it.
fp = open('labeledAbstractSentences.json')
data = json.load(fp)
fp.close()

# data = { k: v for k, v in list(data.items())[:10] }

# Visualizing the data.
for k, v in data.items():
    # k_cleaned = k.translate(str.maketrans('', '', ",.:"))
    # k_split = k_cleaned.strip().split()

    k_split = k.strip().split()

    for w in k_split:
        print(w.lower().translate(str.maketrans('', '', ",.:")), end=' ')
    print()
    for idx, l in enumerate(v):
        print(l, end=' ')
        for _ in range(len(k_split[idx].lower().translate(str.maketrans('', '', ",.:"))) - 1):
            print(' ', end='')
    print()

    assert(len(k_split) == len(v))

muscle cramps are a common problem characterized by a sudden painful involuntary contraction of muscle 
O      O      O   O O      O       O             O  O O      O       O           O           O  O      
these true cramps which originate from peripheral nerves may be distinguished from other muscle pain or spasm 
O     O    O      O     O         O    O          O      O   O  O             O    O     O      O    O  O     
medical history physical examination and a limited laboratory screen help to determine the various causes of muscle cramps 
O       O       O        O           O   O O       O          O      O    O  O         O   O       O      O  O      O      
despite the "benign" nature of cramps many patients find the symptom very uncomfortable 
O       O   O        O      O  O      O    O        O    O   O       O    O             
treatment options are guided both by experience and by a limited number of therapeutic trials 
O         O       O   O      O    O  O          O

#### Splitting Data

In [3]:
random.seed(123)
data_list = list(data.items())
random.shuffle(data_list)

training   = data_list[:6465]
validation = data_list[6465:6845]
testing    = data_list[6845:]

#### Building Count Tables

In [4]:
# Building a vocabulary.
vocabulary = ['']   # Initialize with '' to represent unseen words.
for sentence, _ in training:

    # Set sentence to lowercase, remove extra spaces, split by space.
    sent_split = sentence.lower().strip().split()

    for w in sent_split:

        # For each word, remove punctuation and add to vocabulary if it's not
        # already there.
        word_cleaned = w.translate(str.maketrans('', '', ",.:"))
        if word_cleaned not in vocabulary:
            vocabulary.append(word_cleaned)

print(f'Vocabulary has {len(vocabulary)} total words.')

Vocabulary has 16551 total words.


In [5]:
# Testing the vocabulary.
print(vocabulary.index('quinine'))

7482


In [6]:
# Initialize eta counts table, an np array of dimension (3 x V x 3).
NUM_LABELS = 3
eta_counts = np.ones((NUM_LABELS, len(vocabulary), NUM_LABELS))

In [7]:
# "Functions" that map labels/words to indices.
label_to_int = {'B': 1, 'I': 2, 'O': 0}
word_to_int  = lambda w: vocabulary.index(w.lower())

# Filling the table using training data.
for sentence, labels in training:

    # Pre-process sentence. Zip with word labels.
    sent_split = sentence.lower().strip().split()
    sl_zipped = list(zip(sent_split, labels))

    for idx, (w, l) in enumerate(sl_zipped[:len(sl_zipped)-1]):

        # DEBUGGING
        # print(f'Ziplist length: {len(sl_zipped)} | Curr idx+1: {idx+1}')

        # Remove punctuation from curr word.
        curr_w = w.translate(str.maketrans('', '', ",.:"))

        # The first word in the sentence is counted differently. We pretend
        # that the previous label was 'O'.
        if idx == 0:
            eta_counts[label_to_int['O'], word_to_int(curr_w), label_to_int[l]] += 1

        # Get next word and label. Process next word.
        next_w, next_l = sl_zipped[idx+1]
        next_w = next_w.translate(str.maketrans('', '', ",.:"))

        # Store counts according to current label and next word-label pair.
        eta_counts[label_to_int[l], word_to_int(next_w), label_to_int[next_l]] += 1

In [8]:
# Visualizing the counts table.
for idx, v in enumerate(vocabulary):
    print(f'eta for "{v}" : {eta_counts[:, idx]}')

eta for "" : [[6. 1. 1.]
 [1. 1. 1.]
 [3. 1. 1.]]
eta for "conclusion" : [[109.   1.   1.]
 [  1.   1.   1.]
 [  1.   1.   1.]]
eta for "no" : [[223.   1.   1.]
 [  2.   1.   1.]
 [  1.   1.   1.]]
eta for "single" : [[51.  1.  1.]
 [ 1.  1.  2.]
 [ 1.  1.  1.]]
eta for "level" : [[65.  1.  1.]
 [10.  1.  2.]
 [ 3.  1.  1.]]
eta for "of" : [[5.754e+03 1.000e+00 1.000e+00]
 [6.200e+01 1.000e+00 1.000e+01]
 [2.200e+01 1.000e+00 8.000e+00]]
eta for "beta" : [[11.  6.  1.]
 [ 1.  1.  1.]
 [ 1.  1.  1.]]
eta for "hcg" : [[27.  1.  1.]
 [ 2.  1.  4.]
 [ 1.  1.  1.]]
eta for "is" : [[1.135e+03 1.000e+00 1.000e+00]
 [9.100e+01 1.000e+00 1.000e+00]
 [7.800e+01 1.000e+00 1.000e+00]]
eta for "diagnostic" : [[59.  1.  1.]
 [ 2.  1.  1.]
 [ 1.  1.  1.]]
eta for "ep" : [[3. 1. 1.]
 [1. 1. 1.]
 [1. 1. 1.]]
eta for "and" : [[4.958e+03 1.000e+00 3.000e+00]
 [2.510e+02 1.000e+00 5.000e+00]
 [1.220e+02 1.000e+00 2.000e+00]]
eta for "serial" : [[9. 5. 1.]
 [1. 1. 1.]
 [1. 1. 1.]]
eta for "levels" : [[210.

In [9]:
# Initialize and fill zeta counts table, an np array of dimension (3 x V x V).
zeta_counts = np.ones((NUM_LABELS, len(vocabulary), len(vocabulary)))
for sentence, labels in training:

    # Process sentence, zip with labels.
    sent_split = sentence.lower().strip().split()
    sl_zipped = list(zip(sent_split, labels))

    for idx, (w, l) in enumerate(sl_zipped[:len(sl_zipped)-1]):

        curr_w = w.translate(str.maketrans('', '', ",.:"))

        # Process first word differently.
        if idx == 0:
            zeta_counts[label_to_int['O'], word_to_int(''), word_to_int(curr_w)] += 1

        next_w = sl_zipped[idx+1][0].translate(str.maketrans('', '', ",.:"))

        zeta_counts[label_to_int[l], word_to_int(curr_w), word_to_int(next_w)] += 1

#### Building Frequency Tables

In [10]:
# Initializing freq tables.
eta_freqs  = np.empty_like(eta_counts)
zeta_freqs = np.empty_like(zeta_counts)

In [11]:
# Filling eta_freqs.
for idx in range(NUM_LABELS):
    for jdx in range(len(vocabulary)):
        curr_counts = eta_counts[idx, jdx]
        count_total = np.sum(curr_counts)
        for kdx in range(NUM_LABELS):
            eta_freqs[idx, jdx, kdx] = curr_counts[kdx] / count_total
print(eta_freqs)

[[[0.75       0.125      0.125     ]
  [0.98198198 0.00900901 0.00900901]
  [0.99111111 0.00444444 0.00444444]
  ...
  [0.5        0.25       0.25      ]
  [0.5        0.25       0.25      ]
  [0.5        0.25       0.25      ]]

 [[0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]
  [0.5        0.25       0.25      ]
  ...
  [0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]]

 [[0.6        0.2        0.2       ]
  [0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]
  ...
  [0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]
  [0.33333333 0.33333333 0.33333333]]]


In [12]:
# Testing eta_freqs.
test_count = 0
for row in eta_freqs:
    for col in row:
        if col[1] > col[0] and col[1] > col[2]:
            print(col)
            test_count += 1
print(f'{test_count} total param combos that predict "B"')

[0.47154472 0.52439024 0.00406504]
[0.07692308 0.84615385 0.07692308]
[0.11764706 0.82352941 0.05882353]
[0.2 0.6 0.2]
[0.33333333 0.55555556 0.11111111]
[0.46511628 0.51162791 0.02325581]
[0.20689655 0.75862069 0.03448276]
[0.35714286 0.60714286 0.03571429]
[0.40740741 0.55555556 0.03703704]
[0.31578947 0.63157895 0.05263158]
[0.14285714 0.71428571 0.14285714]
[0.38461538 0.53846154 0.07692308]
[0.28571429 0.66666667 0.04761905]
[0.25 0.5  0.25]
[0.33333333 0.58333333 0.08333333]
[0.38461538 0.53846154 0.07692308]
[0.4        0.53333333 0.06666667]
[0.27272727 0.63636364 0.09090909]
[0.4        0.53333333 0.06666667]
[0.44827586 0.51724138 0.03448276]
[0.44827586 0.53448276 0.01724138]
[0.23076923 0.69230769 0.07692308]
[0.25 0.5  0.25]
[0.11111111 0.77777778 0.11111111]
[0.4 0.5 0.1]
[0.2 0.7 0.1]
[0.33333333 0.55555556 0.11111111]
[0.22222222 0.74074074 0.03703704]
[0.3  0.65 0.05]
[0.22222222 0.72222222 0.05555556]
[0.36363636 0.54545455 0.09090909]
[0.28571429 0.57142857 0.1428571

In [13]:
# Filling zeta_freqs.
for idx in range(NUM_LABELS):
    for jdx in range(len(vocabulary)):
        curr_counts = zeta_counts[idx, jdx]
        count_total = np.sum(curr_counts)
        zeta_freqs[idx, jdx] = curr_counts / count_total
print(zeta_freqs[0])

[[4.34367127e-05 3.90930414e-03 1.73746851e-03 ... 4.34367127e-05
  4.34367127e-05 4.34367127e-05]
 [6.00276127e-05 6.00276127e-05 1.20055225e-04 ... 6.00276127e-05
  6.00276127e-05 6.00276127e-05]
 [5.96160725e-05 5.96160725e-05 5.96160725e-05 ... 5.96160725e-05
  5.96160725e-05 5.96160725e-05]
 ...
 [6.04156597e-05 6.04156597e-05 6.04156597e-05 ... 6.04156597e-05
  6.04156597e-05 6.04156597e-05]
 [6.04156597e-05 6.04156597e-05 6.04156597e-05 ... 6.04156597e-05
  6.04156597e-05 6.04156597e-05]
 [6.04156597e-05 6.04156597e-05 6.04156597e-05 ... 6.04156597e-05
  6.04156597e-05 6.04156597e-05]]


### Predicting
Start by defining helper variables.

In [14]:
# Defining function for getting previous word and label.
def get_prevs(idx, ws, ls) -> tuple[str, int]:
    if idx == 0:
        return '', 0
    else:
        return ws[idx-1], ls[idx-1]

# Defining function for getting the correct eta vector.
def get_eta(prev_label, curr_word):
    if curr_word in vocabulary:
        return eta_freqs[prev_label, word_to_int(curr_word.translate(str.maketrans('', '', ",.:")))]
    else:
        return eta_freqs[prev_label, word_to_int('')]

# Defining function for getting the correct zeta vector.
def get_zeta(prev_label, prev_word):
    if prev_word in vocabulary:
        return zeta_freqs[prev_label, word_to_int(prev_word.translate(str.maketrans('', '', ",.:")))]
    else:
        return zeta_freqs[prev_label, word_to_int('')]

# Defining a Categorical likelihood function.
def CatPMF(x, mu, mode):
    if mode == 'w':
        get_thing = lambda i: vocabulary[i]
    else:
        get_thing = lambda i: [1, 2, 0][i]

    prod = 1
    for idx in range(len(mu)):
        if x == get_thing(idx):
            prod *= mu[idx]
    return prod

#### The Prediction Function
This code should reflect the algorithm overview we gave at the top of the file.

In [15]:
# Defining a function that predicts the labels for a given sentence.
def predict_labels(sentence):

    # Defining lists of words and labels.
    sent_split  = sentence.lower().strip().split()
    label_preds = []

    # Iterating across the sentence and performing label predictions.
    for idx, word in enumerate(sent_split):

        # Getting previous words and labels.
        prev_word, prev_label = get_prevs(idx, sent_split, label_preds)

        # print(f'Curr.     w:{word}')
        # print(f'Prev. l:{prev_label} w:{prev_word}')
        # print()

        # Getting probability vectors.
        eta  = get_eta(prev_label, word)
        # print(eta)
        zeta = get_zeta(prev_label, prev_word)
        # print(zeta)
        # print()

        # DEBUGGING
        if word.translate(str.maketrans('', '', ",.:")) not in vocabulary:
            print("Alert: unseen word")
        else:
            print("Alert: seen word")

        # Creating an objective function.
        objective_function = lambda l: CatPMF(word.translate(str.maketrans('', '', ",.:")), zeta, mode='w') * CatPMF(l, eta, mode='l')

        # print([objective_function(l) for l in [1, 2, 0]], end='\n\n')

        # Optimizing over the objective function and adding to label_preds.
        best_label = np.argmax( [objective_function(l) for l in [1, 2, 0]] )
        label_preds.append(best_label)

    return label_preds

#### Testing

In [16]:
# Here's a list of our testing sentences.
for sent in testing:
    print(sent)

('Results: We confirmed 907 patients with primary nephrotic syndrome (655 definite and 252 presumed patients with FSGS [40%], membranous nephropathy [40%], and minimal change disease [20%]).', ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'B', 'I', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'])
('Patients with non-severe disease randomised to antiviral monoclonal antibodies had lower risk of hospitalisation than those who received placebo: casirivimab-imdevimab (odds ratio (OR) 0.29 (95% CI 0.17 to 0.47); risk difference (RD) -4.2%; moderate certainty), bamlanivimab (OR 0.24 (0.06 to 0.86); RD -4.1%; low certainty), bamlanivimab-etesevimab (OR 0.31 (0.11 to 0.81); RD -3.8%; low certainty), and sotrovimab (OR 0.17 (0.04 to 0.57); RD -4.8%; low certainty).', ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'B', 'I', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'

#### Small Tests

In [17]:
# test_sent = 'Quinine sulfate is an effective medication, but the side-effect profile is worrisome, and other membrane-stabilizing drugs are probably just as effective.'
test_sent = 'Antimalarial drugs such as quinine sulfate'
# test_sent = 'Infectious causes of finger pain include cellulitis, tendinitis, paronychia, felon, and infectious emboli, which generally require antibiotics with or without drainage.'
test_out  = predict_labels(test_sent)
print(test_sent)
for idx, l in enumerate(test_out):
    print(l, end=' ')
    for _ in range(len(test_sent.strip().split()[idx]) - 1):
        print(' ', end='')

Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Antimalarial drugs such as quinine sulfate
0            0     0    0  1       2       

In [18]:
print(eta_freqs[0, word_to_int('Quinine')])
print(vocabulary[np.argmax(zeta_freqs[0, word_to_int('')])])
print()

print( np.argmax(eta_freqs[0, word_to_int('quinine')]) )
print( vocabulary[np.argmax(zeta_freqs[0, word_to_int('')])] )
print()

print( np.argmax(eta_freqs[1, word_to_int('sulfate')]) )
print( vocabulary[np.argmax(zeta_freqs[1, word_to_int('quinine')])] )

[0.25 0.5  0.25]
the

1
the

2
sulfate


#### Evaluation Function

In [19]:
# Function that takes evaluates our baseline
def eval_baseline(test_data):
    '''
    Returns TPs, TNs, FPs, FNs
    `test_data`is a list of sentence-label pairs.
    '''
    tps, tns, fps, fns = 0.0, 0.0, 0.0, 0.0
    for sent, labs in test_data:
        pred_labs = predict_labels(sent)

        assert(len(labs) == len(pred_labs))
        for actual, pred in zip(labs, pred_labs):
            if label_to_int[actual] == pred:
                if pred == 0:
                    tns += 1
                else:
                    tps += 1
            else:
                if pred == 0:
                    fns += 1
                else:
                    fps += 1
    return tps, tns, fps, fns

#### Evaluating the Baseline

In [20]:
tps, tns, fps, fns = eval_baseline(testing)

Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: unseen word
Alert: seen word
Alert: seen word
Alert: unseen

#### For Unshuffled Data
Unseen words appear to be a problem. In the validation set, **11.6%** of encountered words were entirely new to the model. In the testing set, **11.2%** of encountered words were new. I believe the high proportion of unseen words is contributing strongly to our model's low recall score.
#### For Shuffled Data
Unseen words appear to be a problem. In the validation set, **6.07%** of encountered words were entirely new to the model. In the testing set, **6.24%** of encountered words were new. I believe that these unseen words is negatively affecting to our model's recall score.

In [21]:
print(f'TPS: {tps}\nTNS: {tns}\nFPS: {fps}\nFNS: {fns}\n')
acc  = (tps+tns) / (tps + tns + fps + fns)
prec = tps / (tps + fps)
rec  = tps / (tps + fns)
print(f'Accuracy: {round(acc, 4)}')
print(f'Precision: {round(prec, 4)}')   # How often are identified terms actually expert terms?
print(f'Recall: {round(rec, 4)}')       # What percentage of expert terms did we identify?
print(f'F1: {round(2 * (prec * rec) / (prec + rec), 4)}')

TPS: 193.0
TNS: 16423.0
FPS: 79.0
FNS: 444.0

Accuracy: 0.9695
Precision: 0.7096
Recall: 0.303
F1: 0.4246


#### Performance With Unshuffled Data
**Validation Performance**
```c
    TPS: 28.0       Accuracy: 0.9701
    TNS: 7782.0     Precision: 0.4179
    FPS: 39.0       Recall: 0.1217
    FNS: 202.0      F1: 0.1886
```
**Testing Performance**
```c
    TPS: 13.0       Accuracy: 0.9772
    TNS: 16329.0    Precision: 0.2167
    FPS: 47.0       Recall: 0.0375
    FNS: 334.0      F1: 0.0639
```
#### Performance With Shuffled Data
**Validation Performance**
```c
    TPS: 92.0       Accuracy: 0.9697
    TNS: 7967.0     Precision: 0.6216
    FPS: 56.0       Recall: 0.3194
    FNS: 196.0      F1: 0.422
```
**Testing Performance**
```c
    TPS: 193.0      Accuracy: 0.9695
    TNS: 16423.0    Precision: 0.7096
    FPS: 79.0       Recall: 0.303
    FNS: 444.0      F1: 0.4246
```
#### Observations
It seems that our model works is quite reliable when used on words it has seen before. With unseen words reduced to 53.92% of the original percentage, we observed F1 scores increasing by an average of 444.11%. When unseen words make up over 11% of the total encountered words, model performance suffers significantly.


## Upgrade
The upgrade works similarly to the baseline, but with a Dirichlet prior distribution tacked on for more generalized selection of our probability vectors. We predict that our upgrade will allow our program to make more accurate predictions on previously unseen words. 

Here is the equation we'll be working with to make predictions using the Dirichlet prior:
$$p(X_* = v \mid \mu = \mu^{\text{MAP}}) = \frac{n_v + \alpha - 1}{N + V(\alpha - 1)}$$
$n_v$ represents how many times label $v$ occurs in the sentence in the current context window. $N$ is the size of the current context window and $V$ is the size of $\mu$. Finally, $\alpha$ is a parameter for making estimations for $\mu$. It has a size equal to that of $\mu$. We need to construct an $\alpha$ vector to perform our predictions.

Let's begin by defining $\alpha$ as an array of constant values. 

In [22]:
alphas = np.array([1 + 1e-6 for _ in range(NUM_LABELS)])

Let's now program the formula above and find a way to maximize it over different values of $v$.  

In [23]:
# Function that implements the formula above.
def MAP_given_v(n, l):
    prior  = n[l] + alphas[l] - 1
    prior /= np.sum(n) + NUM_LABELS * (alphas[l] - 1)
    return prior

# Function that attempts to perform classification using the function above.
def label_sent_with_upgrade(sent):
    sent_cleaned = sent.lower().strip().split()
    ns = np.zeros(NUM_LABELS)
    preds = []
    for w in sent_cleaned:
        l_pred = np.argmax([MAP_given_v(ns, l) for l in [0, 1, 2]])
        ns[l_pred] += 1
        preds.append(l_pred)
    return preds

In [24]:
# Testing the code we just implemented.
test_sent  = 'Antimalarial drugs such as quinine sulfate'
test_preds = label_sent_with_upgrade(test_sent)
print(test_sent)
for idx, l in enumerate(test_preds):
    print(l, end=' ')
    for _ in range(len(test_sent.strip().split()[idx]) - 1):
        print(' ', end='')

Antimalarial drugs such as quinine sulfate
0            0     0    0  0       0       